In [ ]:
! pip install ffmpy
! chmod +x /Users/sjegan/anaconda3/bin/ffmpeg
! pip install unrar
! pip install beautifulsoup4
! pip install urllib3
! pip install pyunpack
! pip install patool
! pip install webptools
! pip install opencv-python
! pip install setuptools moviepy
! pip install google-api-python-client google-auth-httplib2 google-auth-oauthlib
! pip install pymediainfo
! pip install pydub
! pip install mock
! pip install typed-ast


In [1]:
import pyunpack
from os import listdir
import os
from os.path import isfile, join
import shutil

from unrar import rarfile
import os
import subprocess
import time
from os import listdir
import os
from os.path import isfile, join
import shutil
import glob, os

def getDuration(filename, ppp=False):
    from pymediainfo import MediaInfo
    media_info = MediaInfo.parse(filename)
    #duration in milliseconds
    duration_in_ms = media_info.tracks[0].duration
    if ppp is True:
        print(f'FileDuration --- {filename} = {(round(duration_in_ms/(1000*60)))}')
    return (round(duration_in_ms/(1000*60)))

def getDurationDir(dir_name):
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if isfile(join(dir_name, f))]
    totalfiles = len(onlyfiles)
    onlyfiles.sort()
    i=1
    onlyfiles.sort
    dur = 0
    for loc, filename in onlyfiles:
        if loc.endswith(".avi") or loc.endswith(".mp4") or loc.endswith(".MP4") or loc.endswith(".mkv") or loc.endswith(".mpg") or loc.endswith(".flv"):
            dur += getDuration(loc)
    print(f"Directory in Minutes = {dur}")
    return dur

def convertByPIL(source, destination, small=False):
    from PIL import Image
    image = Image.open(source)
    w1 = image.width
    h1 = image.height
    h2 = 1024
    if(small == True):
        h2 = 512
    w2 = int((w1*h2)/h1)
    newImage = image.resize((w2, h2), Image.NEAREST)
    os.remove(source)
    newImage.save(destination)

def convertByScipy(source, destination, small=False):
    import scipy.misc
    import numpy as np
    img = scipy.misc.imread(imgpath)
    assert len(img.shape) == 3
    w1 = img.shape[0]
    h1 = img.shape[1]
    h2 = 1024
    w2 = int((w1*h2)/h1)

    if small == True:
        if w2 > h2:
            h2 = 512
            w2 = int((w1*h2)/h1)
    img_resized = scipy.misc.imresize(img, (w2, h2))
    img_answer = (img_resized/255.0).astype('float32')

    import matplotlib.pyplot as plt
#     plt.imshow(np.uint8(img))
#     plt.show()
#     plt.imshow(np.uint8(img_resized))
#     plt.show()
    os.remove(source)
    scipy.misc.imsave(destination, img_resized)

def convertImage(source, destination, small=False, delfol = "/Users/sjegan/Downloads/del/"):
    import scipy
    imgpath = source
    try:
        convertByScipy(source, destination, small)
    except:
        try:
            convertByPIL(source, destination, small)
        except:
            print(f'Error in Conversion - {source}')
            shutil.move(src=source, dst=delfol)

def convertAllImages(files, small=False):
    for f in files:
        convertImage(f, f'{f[0:-4]}.jpg', small)

def getListOfFiles(dirName, filterlist):
    listOfFile = os.listdir(dirName)
    allFiles = list()
    for entry in listOfFile:
        fullPath = os.path.join(dirName, entry)
        if os.path.isdir(fullPath):
            allFiles = allFiles + getListOfFiles(fullPath, filterlist)
        else:
            canadd = False
            for f in filterlist:
                if fullPath.endswith(f):
                    allFiles.append(fullPath)
                    break
    allFiles.sort()
                
    return allFiles
def shrinkImages(dir_name):
    from webptools import webplib as webp
    webpFiles = getListOfFiles(dir_name, ['webp'])
    for (w) in webpFiles:
#         webp.dwebp(w,f'{w}.jpg',"-o")
        os.system(f'dwebp "{w}" -o "{w}.jpg"')
        os.remove(w)
    files = getListOfFiles(dir_name, ['jpg', 'jpeg', 'JPEG', 'JPG', 'png', 'PNG'])
    convertAllImages(files, False)

def tomp4(input_file, output_file):
    import time
    getDuration(input_file, True)
    start_time = time.time()
    import ffmpy
    crf = 18
    input_name = input_file
    output_name = output_file
    inp={input_name:None}
    outp = {output_name:'-vcodec libx264 -crf 28 -preset faster -tune film -strict -2 -filter:v scale="640:trunc(ow/a/2)*2" -b:v 128k -b:a 100k -r 20 '}
    outp = {output_name:'-af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale="640:trunc(ow/a/2)*2" -b:v 128k -b:a 100k -r 20 -map 0:v:0 -map 0:a:0 '}
    ff=ffmpy.FFmpeg(inputs=inp,outputs=outp)
    print(ff.cmd) # just to verify that it produces the correct ffmpeg command
    ff.run()
    print(f"---- {output_file} --- {(time.time() - start_time)} seconds ---")
    return (time.time() - start_time)

def tomp4audiovideo(input_file, output_file, audio=0, video=0):
    import time
    getDuration(input_file, True)
    start_time = time.time()
    import ffmpy
    crf = 18
    input_name = input_file
    output_name = output_file
    inp={input_name:None}
    outp = {output_name:'-vcodec libx264 -crf 28 -preset faster -tune film -strict -2 -filter:v scale="640:trunc(ow/a/2)*2" -b:v 128k -b:a 100k -r 20 '}
    outp = {output_name:'-af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale="640:trunc(ow/a/2)*2" -b:v 128k -b:a 100k -r 20 -map 0:a:1 '}
    outp = {output_name:' -map 0:v:0 -map 0:a:1 '}
    ff=ffmpy.FFmpeg(inputs=inp,outputs=outp)
    print(ff.cmd) # just to verify that it produces the correct ffmpeg command
    ff.run()
    print(f"---- {output_file} --- {(time.time() - start_time)} seconds ---")

def chooseAudioVideo(dir_name, dest_dir_name, bin_dir_name, audio=0, video=0):
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if isfile(join(dir_name, f))]
    totalfiles = len(onlyfiles)
    onlyfiles.sort()
    i=1
    onlyfiles.sort
    totalminutes = getDurationDir(dir_name)
    for loc, filename in onlyfiles:
        if loc.endswith(".avi") or loc.endswith(".mp4") or loc.endswith(".MP4") or loc.endswith(".mkv") or loc.endswith(".mpg") or loc.endswith(".flv"):
#             print(loc)
            import datetime
            print(f'-------------------{i} / {totalfiles}----------------------')
#             2 minutes for 23 minutes
#             1 minute for 12 minutes
            import time
            
            print(f'--- Estimate {time.ctime(time.time() + round(totalminutes * 15))}')
            cmd_filelist = "C:\\Users\\Jegan\\Downloads\\ffmpeg\\bin\\ffmpeg.exe -i \"" + loc + "\" -filter:v scale=\"640:trunc(ow/a/2)*2\" -b:v 128k -b:a -bsf:v h264_mp4toannexb 100k -r 20 \"" + dest_dir_name + filename + ".mp4\""
            try:
                dur = getDuration(loc)
                tomp4audiovideo(loc, dest_dir_name + "/" + os.path.splitext(os.path.basename(filename))[0] + ".mp4", audio, video)
                shutil.move(src=loc, dst=bin_dir_name)
                totalminutes -= dur
            except:
                print("*****************FAILED***************" + loc)
            i = i + 1

def tosmmp4(input_file, output_file):
    import ffmpy
    crf = 18
    input_name = input_file
    output_name = output_file
    inp={input_name:None}
    outp = {output_name:'-vcodec libx264 -crf 28 -preset faster -tune film -strict -2 -filter:v scale="640:trunc(ow/a/2)*2" -b:v 128k -b:a 100k -r 20 '}
    outp = {output_name:'-af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale="360:trunc(ow/a/2)*2" -b:v 50k -b:a 30k -r 20 '}
    ff=ffmpy.FFmpeg(inputs=inp,outputs=outp)
#     print(ff.cmd) # just to verify that it produces the correct ffmpeg command
    ff.run()
def shrinkTinyVideos(dir_name, dest_dir_name, bin_dir_name):
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if isfile(join(dir_name, f))]
    totalfiles = len(onlyfiles)
    onlyfiles.sort()
    i=1
    onlyfiles.sort
    for loc, filename in onlyfiles:
        if loc.endswith(".avi") or loc.endswith(".mp4") or loc.endswith(".MP4") or loc.endswith(".mkv") or loc.endswith(".mpg") or loc.endswith(".flv"):
            cmd_filelist = "C:\\Users\\Jegan\\Downloads\\ffmpeg\\bin\\ffmpeg.exe -i \"" + loc + "\" -filter:v scale=\"640:trunc(ow/a/2)*2\" -b:v 128k -b:a 100k -r 20 \"" + dest_dir_name + filename + ".mp4\""
            try:
                tosmmp4(loc, dest_dir_name + "/" + os.path.splitext(os.path.basename(filename))[0] + ".mp4")
                print(loc)
                print(f'-------------------{i} / {totalfiles}----------------------')
                shutil.move(src=loc, dst=bin_dir_name)
            except:
                print("*****************FAILED***************" + loc)
            i = i + 1
from os import listdir
import os
import ffmpy
from os.path import isfile, join
import shutil

def shrinkVideos(dir_name, dest_dir_name, bin_dir_name):
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if isfile(join(dir_name, f))]
    totalfiles = len(onlyfiles)
    onlyfiles.sort()
    i=1
    onlyfiles.sort
    minutestime = []
    totalminutes = getDurationDir(dir_name)
    for loc, filename in onlyfiles:
        if loc.endswith(".avi") or loc.endswith(".mp4") or loc.endswith(".MP4") or loc.endswith(".mkv") or loc.endswith(".mpg") or loc.endswith(".flv"):
#             print(loc)
            import datetime
            print(f'-------------------{i} / {totalfiles}----------------------')
#             2 minutes for 23 minutes
#             1 minute for 12 minutes
            import time
            
            print(f'--- Estimate {time.ctime(time.time() + round(totalminutes * 15))}')
            cmd_filelist = "C:\\Users\\Jegan\\Downloads\\ffmpeg\\bin\\ffmpeg.exe -i \"" + loc + "\" -filter:v scale=\"640:trunc(ow/a/2)*2\" -b:v 128k -b:a -bsf:v h264_mp4toannexb 100k -r 20 \"" + dest_dir_name + filename + ".mp4\""
            try:
                dur = getDuration(loc)
                timetaken = tomp4(loc, dest_dir_name + "/" + os.path.splitext(os.path.basename(filename))[0] + ".mp4")
                minutestime.append((dur, totalminutes))
                shutil.move(src=loc, dst=bin_dir_name)
                totalminutes -= dur
                
            except:
                print("*****************FAILED***************" + loc)
            i = i + 1
#             break
    return minutestime

from bs4 import BeautifulSoup
import urllib3
http = urllib3.PoolManager()
from bs4 import BeautifulSoup
import urllib3
import re

def downloadfile(url, path):
    import urllib3
    http = urllib3.PoolManager()
    r = http.request('GET', url, preload_content=False)

    with open(path, 'wb') as out:
        while True:
            data = r.read(1024 * 1024 * 30)
            if not data:
                break
            out.write(data)

    r.release_conn()


def downloadFromFTP(urls, convert, extension):
    for url in urls:
        response = http.request('GET', url)
        print(response)
        soup = BeautifulSoup(response.data)
        links = []
        import os
        i = 0
        t = True

        for link in soup.findAll('a', attrs={'href': re.compile(extension)}):
            i = i + 1
#             if '1-25.flv' == link.get('href'):
#                 t = True
            if i > 10 and link.get('href') not in links and t == True:
                links.append(link.get('href'))
                print(link.get('href'))
                downloadfile(url+link.get('href'), convert + os.path.basename( link.get('href')))


import os
import subprocess
import time
from os import listdir
import os
from os.path import isfile, join
import shutil

def removeHyphen(dir_name):
    import shutil
    from os import listdir
    video_files = video_files_ffmpeg
    base_dir = dir_name

    files = []
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if isfile(join(dir_name, f))]
    onlyfiles.sort()
    for loc, filename in onlyfiles:
        if loc.endswith(extension):
            files.append(loc)
    for f in files:
        if f.find("\'") != -1:
            r = f.replace("\'", "")
            shutil.move(src=f, dst=r)

def concatenateFiles(dir_name, video_files_ffmpeg, extension, output_file, group=None):
    removeHyphen(dir_name)
    
    import time
    totalminutes = getDurationDir(dir_name)
    print(f'--- Estimate {time.ctime(time.time() + round(totalminutes * 254 / 851))}')
    start_time = time.time()
    
    video_files = video_files_ffmpeg
    base_dir = dir_name

    files = []
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if isfile(join(dir_name, f))]
    onlyfiles.sort()
    for loc, filename in onlyfiles:
        if loc.endswith(extension):
            files.append(loc)
    files.sort()
    if group == None:
        group = len(files)
    i = 0
    tempfiles = []
    for f in files:
        tempfiles.append(f)
        i = i + 1

        if i % group == 0:
            file_list = open(video_files, "w")
            for tee in tempfiles:
                file_list.write("file '%s'\n" % tee)
            file_list.close()
            cmd = ["ffmpeg",
                   "-f",
                   "concat",
                   "-safe",
                   "0",
                   "-loglevel",
                   "quiet",
                   "-i",
                   "%s" % video_files,
                   "-c",
                   "copy",
                   "%s" % (output_file + str(i)+".mp4")
                   ]
            p = subprocess.Popen(cmd, stdin=subprocess.PIPE)
            fout = p.stdin
            fout.close()
            p.wait()
            print(p.returncode)
            tempfiles = []
    if len(tempfiles) > 0:
        file_list = open(video_files, "w")
        for tee in tempfiles:
            file_list.write("file '%s'\n" % tee)
        file_list.close()
        cmd = ["ffmpeg",
               "-f",
               "concat",
               "-safe",
               "0",
               "-loglevel",
               "quiet",
               "-i",
               "%s" % video_files,
               "-c",
               "copy",
               "%s" % (output_file + str(i)+".mp4")
               ]
        p = subprocess.Popen(cmd, stdin=subprocess.PIPE)
        fout = p.stdin
        fout.close()
        p.wait()
        print(p.returncode)
        tempfiles = []
    
    print(f"---- {output_file} --- {(time.time() - start_time)} seconds ---")
    return (time.time() - start_time)
        

import zipfile
from unrar import rarfile
import os
import subprocess
import time
from os import listdir
import os
from os.path import isfile, join
import shutil
import glob, os

def extractZip(dir_name, convert, delfol):
    loop = True
    kkk = 0
    while(loop == True):
        os.chdir(dir_name)
        unpacked = 0
        result = []
        for file in glob.glob("*.cbr"):
            result.append(dir_name + file)
        for file in glob.glob("*.cbz"):
            result.append(dir_name + file)
        for file in glob.glob("*.zip"):
            result.append(dir_name + file)
        for file in glob.glob("*.rar"):
            result.append(dir_name + file)


        import shutil

        for loc in result:
            shutil.move(src=loc, dst=convert)

        os.chdir(convert)
        result = []
        for file in glob.glob("**/*.cbr", recursive=True):
            result.append((convert +file, file[0:-4]))
        for file in glob.glob("**/*.cbz", recursive=True):
            result.append((convert + file, file[0:-4]))
        for file in glob.glob("**/*.rar", recursive=True):
            result.append((convert + file, file[0:-4]))
        for file in glob.glob("**/*.zip", recursive=True):
            result.append((convert + file, file[0:-4]))
        if len(result) == 0:
            loop = False
            
        for (filename, title) in result:
            os.system(f'mkdir "{convert+title}"')
            import subprocess
            params = f' x -o+ "{filename}" *.* "{convert+title}"'
            print(os.path.dirname(convert+title), "|", convert+title)
    #         try:
    #             rar = rarfile.RarFile(filename)
    #             rar.extractall(convert+title)

    #         except:
    #             rar = zipfile.ZipFile(filename)
    #             rar.extractall(convert+title)
            pyunpack.Archive(filename).extractall(convert+title)

            params = ''
            deleteplace = convert+"delete"
            shutil.move(src=filename, dst=delfol+"/"+os.path.basename(filename)+str(kkk))
            kkk = kkk + 1
#             dir_name = "/Users/sjegan/Downloads/com2/"
            restucturedir(convert)

        print("done")
    restucturedir(convert)


def restructure(onlyfiles):
    for (subf, title) in onlyfiles:
#         print(subf)
        files = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isfile(join(subf, f))]
        for (filename, title) in files:
            if "zzz" in title:
                os.remove(filename)
        folders = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isdir(join(subf, f))]
        if len(files) == 0 and len(folders) == 0:
            shutil.rmtree(subf)
            continue
        if len(files) == 0 and len(folders) == 1:
#             print("YES")

            for (fold, title) in folders:
                subfiles = [(join(fold, f), f) for f in listdir(fold) if (not f.endswith('DS_Store'))]

#                 print(fold, "|",subf)
                for (subfile, titlesub) in subfiles:
                    shutil.move(src=subfile,dst=subf)
        onlyfiles = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isdir(join(subf, f))]
        restructure(onlyfiles)

def restucturedir(dir_name):
    files = []
    folders = []
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if (not f.endswith('DS_Store')) and os.path.isdir(join(dir_name, f))]
    onlyfiles.sort()
    restructure(onlyfiles)

def extractNShrink(dir_name, convert, delfol, finaldir):
    extractZip(dir_name, convert, delfol)
    shrinkImages(convert)
    onlyfiles = [(join(convert, f), f) for f in listdir(convert) if (not f.endswith('DS_Store'))]
    for (f,t) in onlyfiles:
        shutil.move(src=f, dst=finaldir)


def numberingFiles(dir_name):
    files = []
    folders = []
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if (not f.endswith('DS_Store')) and os.path.isdir(join(dir_name, f))]
    onlyfiles.sort()

    for (subf, title) in onlyfiles:
    #         print(subf)
        files = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isfile(join(subf, f))]
        folders = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isdir(join(subf, f))]
        if len(folders) > 0:
            os.chdir(subf)
            result = []
            for file in glob.glob("**/*.jpg", recursive=True):
                result.append((subf + "/"+file, file))
            for file in glob.glob("**/*.jpeg", recursive=True):
                result.append((subf + "/"+ file, file))
            for file in glob.glob("**/*.JPG", recursive=True):
                result.append((subf + "/"+ file, file))
            for file in glob.glob("**/*.JPEG", recursive=True):
                result.append((subf + "/"+ file, file))
            for file in glob.glob("**/*.png", recursive=True):
                result.append((subf + "/"+ file, file))
            for file in glob.glob("**/*.PNG", recursive=True):
                result.append((subf + "/"+ file, file))
            result.sort()
            digits = 1 if len(result) < 10 else (2 if len(result) < 100 else (3 if len(result) < 1000 else 4))
            j = 1
            for (r, title) in result:
                dest = (f'{subf}/{str(j).zfill(digits)} {os.path.basename(title)}')
                shutil.move(src=r, dst=dest)
                j = j+1

        restucturedir(dir_name)
        restucturedir(dir_name)
        restucturedir(dir_name)

def makeZips(dirName):
    import shutil
    listOfFile = os.listdir(dirName)
    allFiles = list()
    for entry in listOfFile:
        fullPath = os.path.join(dirName, entry)
        if os.path.isdir(fullPath):
    #         print(fullPath)
            shutil.make_archive(fullPath, 'zip', fullPath)
            shutil.rmtree(fullPath)

def renameNRestructure(dir_name):
    files = []
    folders = []
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if (not f.endswith('DS_Store')) and os.path.isdir(join(dir_name, f))]
    onlyfiles.sort()

    for (subf, title) in onlyfiles:
    #         print(subf)
#         print(title)
        title2 = title
        files = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isfile(join(subf, f))]
        folders = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isdir(join(subf, f))]
        if len(folders) > 0:
            os.chdir(subf)
            result = []
            for file in glob.glob("**/*.jpg", recursive=True):
                result.append((subf + "/"+file, file))
            for file in glob.glob("**/*.jpeg", recursive=True):
                result.append((subf + "/"+ file, file))
            for file in glob.glob("**/*.JPG", recursive=True):
                result.append((subf + "/"+ file, file))
            for file in glob.glob("**/*.JPEG", recursive=True):
                result.append((subf + "/"+ file, file))
            for file in glob.glob("**/*.png", recursive=True):
                result.append((subf + "/"+ file, file))
            for file in glob.glob("**/*.PNG", recursive=True):
                result.append((subf + "/"+ file, file))
            result.sort()
            digits = 1 if len(result) < 10 else (2 if len(result) < 100 else (3 if len(result) < 1000 else 4))
            j = 1
            for (r, title) in result:
                dest = (f'{subf}/{title2}{str(j).zfill(digits)} {os.path.basename(title)}')
    #             print(dest)
    #             break
                shutil.move(src=r, dst=dest)
                j = j+1

        restucturedir(dir_name)
        restucturedir(dir_name)
        restucturedir(dir_name)
        
def removeTxt(dir_name):
    files = []
    folders = []
    onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if (not f.endswith('DS_Store')) and os.path.isdir(join(dir_name, f))]
    onlyfiles.sort()

    for (subf, title) in onlyfiles:
    #         print(subf)
#         print(title)
        title2 = title
        files = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isfile(join(subf, f))]
        folders = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isdir(join(subf, f))]
        if len(folders) > 0:
            os.chdir(subf)
            result = []
            for file in glob.glob("**/*.txt", recursive=True):
                result.append((subf + "/"+file, file))
            result.sort()
            for (r, title) in result:
                os.remove(r)

        restucturedir(dir_name)
        restucturedir(dir_name)
        restucturedir(dir_name)

In [2]:

dir_name = "/Users/sjegan/Downloads/untitled folder 3"
dest_dir_name = "/Users/sjegan/Downloads/dest"
bin_dir_name = "/Users/sjegan/Downloads/dest/del"

minutestime = shrinkVideos(dir_name, dest_dir_name, bin_dir_name)



Directory in Minutes = 2830
-------------------1 / 62----------------------
--- Estimate Wed Nov  6 12:55:44 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S01E01.480p.mkv = 58
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S01E01.480p.mkv" -af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale=640:trunc(ow/a/2)*2 -b:v 128k -b:a 100k -r 20 -map 0:v:0 -map 0:a:0 /Users/sjegan/Downloads/dest/Breaking.Bad.S01E01.480p.mp4
---- /Users/sjegan/Downloads/dest/Breaking.Bad.S01E01.480p.mp4 --- 490.1714780330658 seconds ---
-------------------2 / 62----------------------
--- Estimate Wed Nov  6 12:49:24 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S01E02.480p.mkv = 48
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S01E02.480p.mkv" -af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 

---- /Users/sjegan/Downloads/dest/Breaking.Bad.S02E07.480p.mp4 --- 194.5547640323639 seconds ---
-------------------15 / 62----------------------
--- Estimate Wed Nov  6 11:15:16 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S02E08.480p.mkv = 45
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S02E08.480p.mkv" -af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale=640:trunc(ow/a/2)*2 -b:v 128k -b:a 100k -r 20 -map 0:v:0 -map 0:a:0 /Users/sjegan/Downloads/dest/Breaking.Bad.S02E08.480p.mp4
---- /Users/sjegan/Downloads/dest/Breaking.Bad.S02E08.480p.mp4 --- 198.25315594673157 seconds ---
-------------------16 / 62----------------------
--- Estimate Wed Nov  6 11:07:19 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S02E09.480p.mkv = 45
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S02E09.480p.mkv" -af apad

---- /Users/sjegan/Downloads/dest/Breaking.Bad.S03E09.480p.BluRay.X264.mp4 --- 449.7255210876465 seconds ---
-------------------28 / 62----------------------
--- Estimate Wed Nov  6 09:55:30 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S03E10.480p.BluRay.X264.mkv = 47
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S03E10.480p.BluRay.X264.mkv" -af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale=640:trunc(ow/a/2)*2 -b:v 128k -b:a 100k -r 20 -map 0:v:0 -map 0:a:0 /Users/sjegan/Downloads/dest/Breaking.Bad.S03E10.480p.BluRay.X264.mp4
---- /Users/sjegan/Downloads/dest/Breaking.Bad.S03E10.480p.BluRay.X264.mp4 --- 286.8720591068268 seconds ---
-------------------29 / 62----------------------
--- Estimate Wed Nov  6 09:48:32 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S03E11.480p.BluRay.X264.mkv = 47
ffmpeg -i "/Users/sj

---- /Users/sjegan/Downloads/dest/Breaking.Bad.S04E09.480p.mp4 --- 205.89447498321533 seconds ---
-------------------41 / 62----------------------
--- Estimate Wed Nov  6 08:31:48 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S04E10.480p.mkv = 47
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S04E10.480p.mkv" -af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale=640:trunc(ow/a/2)*2 -b:v 128k -b:a 100k -r 20 -map 0:v:0 -map 0:a:0 /Users/sjegan/Downloads/dest/Breaking.Bad.S04E10.480p.mp4
---- /Users/sjegan/Downloads/dest/Breaking.Bad.S04E10.480p.mp4 --- 224.89586997032166 seconds ---
-------------------42 / 62----------------------
--- Estimate Wed Nov  6 08:23:48 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S04E11.480p.mkv = 47
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S04E11.480p.mkv" -af apa

---- /Users/sjegan/Downloads/dest/Breaking.Bad.S05E09.480p.mp4 --- 225.86315894126892 seconds ---
-------------------54 / 62----------------------
--- Estimate Wed Nov  6 06:47:04 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S05E10.480p.mkv = 47
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S05E10.480p.mkv" -af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale=640:trunc(ow/a/2)*2 -b:v 128k -b:a 100k -r 20 -map 0:v:0 -map 0:a:0 /Users/sjegan/Downloads/dest/Breaking.Bad.S05E10.480p.mp4
---- /Users/sjegan/Downloads/dest/Breaking.Bad.S05E10.480p.mp4 --- 237.30172204971313 seconds ---
-------------------55 / 62----------------------
--- Estimate Wed Nov  6 06:39:17 2019
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S05E11.480p.mkv = 47
ffmpeg -i "/Users/sjegan/Downloads/untitled folder 3/Breaking.Bad.S05E11.480p.mkv" -af apa

In [ ]:

shrinkImages("/Users/sjegan/Downloads/uuu/")

/Users/sjegan/Downloads/untitled folder 3/Death Note 02.mkv
-------------------1 / 180----------------------
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Death Note 02.mkv = 23
*****************FAILED***************/Users/sjegan/Downloads/untitled folder 3/Death Note 02.mkv
/Users/sjegan/Downloads/untitled folder 3/Death Note 03.mkv
-------------------2 / 180----------------------
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Death Note 03.mkv = 23
*****************FAILED***************/Users/sjegan/Downloads/untitled folder 3/Death Note 03.mkv
/Users/sjegan/Downloads/untitled folder 3/Death Note 04.mkv
-------------------3 / 180----------------------
FileDuration --- /Users/sjegan/Downloads/untitled folder 3/Death Note 04.mkv = 23
*****************FAILED***************/Users/sjegan/Downloads/untitled folder 3/Death Note 04.mkv
/Users/sjegan/Downloads/untitled folder 3/Death Note 05.mkv
-------------------4 / 180----------------------
FileDuration --- /Users/

In [3]:

dir_name = "/Users/sjegan/Downloads/untitled folder 3"
dest_dir_name = "/Users/sjegan/Downloads/dest"
bin_dir_name = "/Users/sjegan/Downloads/dest/del"
shrinkTinyVideos(dir_name, dest_dir_name, bin_dir_name)


/Users/sjegan/Downloads/untitled folder 3/Burra katha 2019 www.9kmovies.asia Dual Audio Hindi 400MB UNCUT HDRip.mkv
-------------------1 / 11----------------------
/Users/sjegan/Downloads/untitled folder 3/Degree Wala Teacher (Charmsukh) S01 2019 www.9kmovies.asia Hindi Ullu Web Series 720p HDRip 150MB.mkv
-------------------2 / 11----------------------
/Users/sjegan/Downloads/untitled folder 3/Faltu (2019) S01 EP3 www.9kmovies.trade Fliz Movies Hindi Hot Web Series 720p HDRip 100MB.mkv
-------------------3 / 11----------------------
/Users/sjegan/Downloads/untitled folder 3/Indian Lovers smooching and pussy press in public - XVIDEOS.COM.mp4
-------------------4 / 11----------------------
/Users/sjegan/Downloads/untitled folder 3/Indian lady super figure getting with husband friend - XVIDEOS.COM.mp4
-------------------5 / 11----------------------
/Users/sjegan/Downloads/untitled folder 3/Khuda Aur Mohabbat 2019 Urdu 01 (Ep.1-12) www.9kmovies.trade Web Series 480p HDRip 1.2GB.mkv
------

In [4]:

urls = ['http://94.130.23.244/TV%20Shows%20A/Narcos/Season%201/',
        'http://94.130.23.244/TV%20Shows%20A/Narcos/Season%202/',
        'http://94.130.23.244/TV%20Shows%20A/Narcos/Season%203/', 
        ]
convert = "/Users/sjegan/Downloads/com2/"
extension = "mkv"
downloadFromFTP(urls, convert, extension)


In [22]:

dir_name = "/Users/sjegan/Downloads/concat"

video_files_ffmpeg = "/Users/sjegan/Downloads/video_list.txt"
output_file = "/Users/sjegan/Downloads/BBB"
extension = ".mp4"

concatenateFiles(dir_name, video_files_ffmpeg, extension, output_file, group=None)





0


In [ ]:
dir_name = "/Users/sjegan/Downloads/com/"
convert = "/Users/sjegan/Downloads/com2/"
delfol = "/Users/sjegan/Downloads/del/"
extractZip(dir_name, convert, delfol)


In [ ]:
dir_name = "/Users/sjegan/Downloads/com2/"
restucturedir(dir_name)


In [ ]:
dir_name = "/Users/sjegan/Downloads/com/"
convert = "/Users/sjegan/Downloads/com2/"
delfol = "/Users/sjegan/Downloads/del/"
finaldir = "/Users/sjegan/Downloads/uuu/"
extractNShrink(dir_name, convert, delfol, finaldir)
# numberingFiles(finaldir)

In [ ]:
finaldir = "/Users/sjegan/Downloads/uuu/"

numberingFiles(finaldir)

In [ ]:

dirName = '/Users/sjegan/Downloads/uuu'
makeZips(dirName)


In [ ]:
dir_name = '/Users/sjegan/Downloads/uuu'


removeTxt(dir_name)

In [ ]:
dir_name = '/Users/sjegan/Downloads/uuu'
renameNRestructure(dir_name)

In [ ]:
dir_name = '/Users/sjegan/Downloads/uuu'
files = []
folders = []
onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if (not f.endswith('DS_Store')) and os.path.isdir(join(dir_name, f))]
onlyfiles.sort()

for (subf, title) in onlyfiles:
#         print(subf)
#         print(title)
    title2 = title
    files = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isfile(join(subf, f))]
    folders = [(join(subf, f), f) for f in listdir(subf) if (not f.endswith('DS_Store')) and os.path.isdir(join(subf, f))]
    if len(folders) > 0:
        os.chdir(subf)
        result = []
        for file in glob.glob("**/*.jpg", recursive=True):
            result.append((subf + "/"+file, file))
        for file in glob.glob("**/*.jpeg", recursive=True):
            result.append((subf + "/"+ file, file))
        for file in glob.glob("**/*.JPG", recursive=True):
            result.append((subf + "/"+ file, file))
        for file in glob.glob("**/*.JPEG", recursive=True):
            result.append((subf + "/"+ file, file))
        for file in glob.glob("**/*.png", recursive=True):
            result.append((subf + "/"+ file, file))
        for file in glob.glob("**/*.PNG", recursive=True):
            result.append((subf + "/"+ file, file))
        result.sort()
        digits = 1 if len(result) < 10 else (2 if len(result) < 100 else (3 if len(result) < 1000 else 4))
        j = 1
        for (r, title) in result:
            dest = (f'{subf}/{title2}{str(j).zfill(digits)} {os.path.basename(title)}')
#             print(dest)
#             break
            shutil.move(src=r, dst=dest)
            j = j+1

    restucturedir(dir_name)
    restucturedir(dir_name)
    restucturedir(dir_name)

In [ ]:
import cv2
import numpy as np
inputfile = '/Users/sjegan/Downloads/uuu/'
outputfile = '/Users/sjegan/Downloads/BBB2.mp4'
cap = cv2.VideoCapture('C:/New folder/video.avi')
 
fourcc = cv2.VideoWriter_fourcc(*'XVID')
out = cv2.VideoWriter('output.avi',fourcc, 5, (480,360))
 
while True:
    ret, frame = cap.read()
    if ret == True:
        b = cv2.resize(frame,(480,360),fx=0,fy=0, interpolation = cv2.INTER_CUBIC)
        out.write(b)
    else:
        break
    
cap.release()
out.release()
cv2.destroyAllWindows()

In [ ]:
import cv2

In [ ]:
import cv2
import numpy as np
inputfile = '/Users/sjegan/Downloads/concat/YouTube.mp4'
outputfile = '/Users/sjegan/Downloads/YouTube.mp4'

cap = cv2.VideoCapture(inputfile)
 
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter(outputfile,fourcc, 20, (480,360))
 
while True:
    ret, frame = cap.read()
    if ret == True:
        b = cv2.resize(frame,(480,360),fx=0,fy=0, interpolation = cv2.INTER_NEAREST)
        out.write(b)
    else:
        break
    
cap.release()
out.release()
cv2.destroyAllWindows()

In [ ]:
import moviepy.editor as mp
clip = mp.VideoFileClip(inputfile)
clip_resized = clip.resize(height=360) # make the height 360px ( According to moviePy documenation The width is then computed so that the width/height ratio is conserved.)
clip_resized.write_videofile(outputfile)

In [ ]:
input_file = '/Users/sjegan/Downloads/concat/BBB186.mp4'
output_file = '/Users/sjegan/Downloads/YouTube.mp4'
import ffmpy
crf = 18
input_name = input_file
output_name = output_file
inp={input_name:None}
outp = {output_name:'-af apad -shortest -avoid_negative_ts make_zero -fflags +genpts -vcodec libx264 -acodec aac -preset faster -tune film -strict -2 -filter:v scale="360:trunc(ow/a/2)*2" -b:v 50k -b:a 30k -r 20 '}

ff=ffmpy.FFmpeg(inputs=inp,outputs=outp)
print(ff.cmd) # just to verify that it produces the correct ffmpeg command
ff.run()

In [23]:
import pickle
import os.path
from googleapiclient.discovery import build
from google_auth_oauthlib.flow import InstalledAppFlow
from google.auth.transport.requests import Request

# If modifying these scopes, delete the file token.pickle.
SCOPES = ['https://www.googleapis.com/auth/drive.metadata.readonly']

def runtest():
    """Shows basic usage of the Drive v3 API.
    Prints the names and ids of the first 10 files the user has access to.
    """
    creds = None
    # The file token.pickle stores the user's access and refresh tokens, and is
    # created automatically when the authorization flow completes for the first
    # time.
    if os.path.exists('token.pickle'):
        with open('token.pickle', 'rb') as token:
            creds = pickle.load(token)
    # If there are no (valid) credentials available, let the user log in.
    if not creds or not creds.valid:
        if creds and creds.expired and creds.refresh_token:
            creds.refresh(Request())
        else:
            flow = InstalledAppFlow.from_client_secrets_file(
                '/Users/sjegan/Downloads/tomdickcredentials.json', SCOPES)
            creds = flow.run_local_server(port=0)
        # Save the credentials for the next run
        with open('token.pickle', 'wb') as token:
            pickle.dump(creds, token)

    service = build('drive', 'v3', credentials=creds)

    # Call the Drive v3 API
    results = service.files().list(
        pageSize=10, fields="nextPageToken, files(id, name)").execute()
    items = results.get('files', [])

    if not items:
        print('No files found.')
    else:
        print('Files:')
        for item in items:
            print(u'{0} ({1})'.format(item['name'], item['id']))
runtest()

ValueError: Client secrets must be for a web or installed app.

In [ ]:
from os.path import join, dirname
from googleapiclient.discovery import build
from httplib2 import Http
from oauth2client import file, client, tools
SCOPES = 'https://www.googleapis.com/auth/photoslibrary.readonly'

store = file.Storage(join(dirname(__file__), 'token-for-google.json'))
creds = store.get()
if not creds or creds.invalid:
    flow = client.flow_from_clientsecrets(join(dirname(__file__), 'client_id.json', SCOPES))
    creds = tools.run_flow(flow, store)
google_photos = build('photoslibrary', 'v1', http=creds.authorize(Http()))

day, month, year = ('0', '6', '2019')  # Day or month may be 0 => full month resp. year
date_filter = [{"day": day, "month": month, "year": year}]  # No leading zeroes for day an month!
nextpagetoken = 'Dummy'
while nextpagetoken != '':
    nextpagetoken = '' if nextpagetoken == 'Dummy' else nextpagetoken
    results = google_photos.mediaItems().search(
            body={"filters":  {"dateFilter": {"dates": [{"day": day, "month": month, "year": year}]}},
                  "pageSize": 10, "pageToken": nextpagetoken}).execute()
    # The default number of media items to return at a time is 25. The maximum pageSize is 100.
    items = results.get('mediaItems', [])
    nextpagetoken = results.get('nextPageToken', '')
    for item in items:
            print(f"{item['filename']} {item['mimeType']} '{item.get('description', '- -')}'"
                      f" {item['mediaMetadata']['creationTime']}\nURL: {item['productUrl']}")

In [51]:
from pytube import YouTube 
SAVE_PATH = "E:/" #to_do 
i = 1

def downloadYoutube(link):
#     link="https://www.youtube.com/watch?v=e6_hbN-KDxs"
    try:
        yt = YouTube(link)
    except:
        print(link + " - Unavailable")
        return
    ttt = yt.streams.filter(subtype='mp4').all()
    for t in ttt:
        if t.resolution == "360p":
            t.download('/Users/sjegan/Downloads/concat/')
            break
        
for line in test.split('\n'):
    if line.find('watch') > -1:
#         print(line)
        downloadYoutube(line)

        
        
# ttt[0].download('/Users/sjegan/Downloads/concat/')

# yt.download('/path/to/download/directory')
# ttt

https://www.youtube.com/watch?v=9z0CqBfv0yY - Unavailable
https://www.youtube.com/watch?v=frYxeK8wGGg - Unavailable
https://www.youtube.com/watch?v=EmMq3F5NM4I - Unavailable
https://www.youtube.com/watch?v=QMjttbi1LqY - Unavailable
https://www.youtube.com/watch?v=4QAmSrf0Nc8 - Unavailable
https://www.youtube.com/watch?v=DxmuMJHIg2Y - Unavailable
https://www.youtube.com/watch?v=MCH6M876l9A - Unavailable
https://www.youtube.com/watch?v=W7uZBZKsYvk - Unavailable
https://www.youtube.com/watch?v=1cfG_fGPSWQ - Unavailable
https://www.youtube.com/watch?v=TlTgYJGqpQ8 - Unavailable
https://www.youtube.com/watch?v=JCOSgpH5CD0 - Unavailable
https://www.youtube.com/watch?v=BZnW1A3Xgk0 - Unavailable
https://www.youtube.com/watch?v=D8FS0PTicFs - Unavailable
https://www.youtube.com/watch?v=AbFUJVsSVxQ - Unavailable
https://www.youtube.com/watch?v=5xobEYENs8M - Unavailable
https://www.youtube.com/watch?v=seq3d8aNOn4 - Unavailable
https://www.youtube.com/watch?v=bE_5J2vNV3c - Unavailable
https://www.yo

'La vecina | Ricardo logra engañar a Isabel.mp4'

In [10]:
! pip install pytube

In [7]:
files_final

[]

In [9]:
for line in test.split('\n'):
    print(line)
    break

https://www.youtube.com/watch?v=e6_hbN-KDxs


In [8]:
import libLPAPFF

ModuleNotFoundError: No module named 'libLPAPFF'

In [3]:
dir_name = "/Users/sjegan/Downloads/concat"

video_files_ffmpeg = "/Users/sjegan/Downloads/video_list.txt"
output_file = "/Users/sjegan/Downloads/BBB"
extension = ".mp4"
group = 10

from moviepy.editor import VideoFileClip, concatenate_videoclips

# def concatenateFiles(dir_name, video_files_ffmpeg, extension, output_file, group=None):
removeHyphen(dir_name)
video_files = video_files_ffmpeg
base_dir = dir_name

files = []
onlyfiles = [(join(dir_name, f), f) for f in listdir(dir_name) if isfile(join(dir_name, f))]
onlyfiles.sort()
for loc, filename in onlyfiles:
    if loc.endswith(extension):
        files.append(loc)
files.sort()




if group == None:
    group = len(files)
i = 0
tempfiles = []
for f in files:
    tempfiles.append(f)
    i = i + 1

    if i % group == 0:
        files_final = []
        for tee in tempfiles:
            files_final.append(VideoFileClip(tee))

        final_clip = concatenate_videoclips(files_final)
        final_clip.write_videofile(output_file + str(i) + extension)

        for o in files_final:
            o.__del__()
        tempfiles = []
if len(tempfiles) > 0:
    files_final = []
    for tee in tempfiles:
        files_final.append(VideoFileClip(tee))
    final_clip = concatenate_videoclips(files_final)
    final_clip.write_videofile(output_file + str(i) + extension)
    for o in files_final:
        o.__del__()
    tempfiles = []







print("0")

chunk:   0%|          | 35/292928 [00:00<14:19, 340.91it/s, now=None]

Moviepy - Building video /Users/sjegan/Downloads/BBB10.mp4.
MoviePy - Writing audio in %s


t:   0%|          | 3/265694 [00:00<2:45:59, 26.68it/s, now=None]        

MoviePy - Done.
Moviepy - Writing video /Users/sjegan/Downloads/BBB10.mp4



Moviepy - Done !
Moviepy - video ready /Users/sjegan/Downloads/BBB10.mp4


AttributeError: 'VideoFileClip' object has no attribute '__del__'

In [ ]:
import moviepy.editor as mpe
my_clip = mpe.VideoFileClip('some_clip.mp4')
audio_background = mpe.AudioFileClip('some_background.mp3')
final_audio = mpe.CompositeAudioClip([my_clip.audio, audio_background])
final_clip = my_clip.set_audio(final_audio)

In [4]:
filename = "/Users/sjegan/Downloads/untitled folder 3/Death Note 02.mkv"
from pymediainfo import MediaInfo
media_info = MediaInfo.parse(filename)
#duration in milliseconds
duration_in_ms = media_info.tracks[0].duration
print(round(duration_in_ms/(1000*60)))

23


In [11]:
dir_name = "/Users/sjegan/Downloads/untitled folder 3"
dest_dir_name = "/Users/sjegan/Downloads/dest"
bin_dir_name = "/Users/sjegan/Downloads/dest/del"
# shrinkVideos(dir_name, dest_dir_name, bin_dir_name)




In [12]:
dur

9829

In [2]:
import datetime
datetime.datetime.now() + datetime.timedelta(minutes = round(9000 * 12))

datetime.datetime(2020, 1, 13, 4, 38, 57, 734236)

In [9]:
import time
time.ctime(time.time() + round(9000 * 15))

'Thu Oct 31 18:12:51 2019'

In [8]:
time.ctime(time.time()+ )

'Wed Oct 30 04:43:06 2019'

In [ ]:
12 min 60 sec
1 min 15 sec
9000 * 15


In [22]:
from pydub import AudioSegment
sound = AudioSegment.from_file('/Users/sjegan/Downloads/Review/test.wav')
# octaves = 0.5
# new_sample_rate = int(sound.frame_rate * (2.0 ** octaves))
# chipmunk_sound = sound._spawn(sound.raw_data, overrides={'frame_rate': new_sample_rate})
chipmunk_sound = sound._spawn(sound.raw_data)
chipmunk_ready_to_export = chipmunk_sound.speedup(playback_speed=1.2)
chipmunk_ready_to_export.export('/Users/sjegan/Downloads/Review/test2.mp3', format="mp3")

<_io.BufferedRandom name='/Users/sjegan/Downloads/Review/test2.mp3'>

In [13]:
chipmunk_ready_to_export

<_io.BufferedRandom name='/Users/sjegan/Downloads/Review/test2.wav'>

In [37]:
import moviepy.editor as mpe
my_clip = mpe.VideoFileClip('/Users/sjegan/Downloads/Review/joker.mp4')
audio_background = mpe.AudioFileClip('/Users/sjegan/Downloads/Review/test2.mp3')
final_audio = mpe.CompositeAudioClip([my_clip.audio.fx(mpe.afx.volumex, 0.2), audio_background])
# final_audio = mpe.CompositeAudioClip([my_clip.audio])
final_clip = my_clip.set_audio(final_audio)

txt_clip = mpe.TextClip("Joker Movie Review", fontsize=12, color='white').set_pos("right", "bottom")
burn_video = mpe.CompositeVideoClip([final_clip, txt_clip])
# final_clip.write_videofile('/Users/sjegan/Downloads/Review/joker2.mp4', fps=60, codec="mpeg4")
burn_video.write_videofile('/Users/sjegan/Downloads/Review/joker2.mp4', 
                     codec='libx264', 
                     audio_codec='aac', 
                     temp_audiofile='/Users/sjegan/Downloads/Review//temp-audio.m4a', 
                     remove_temp=True
                     )

OSError: MoviePy Error: creation of None failed because of the following error:

[Errno 2] No such file or directory: 'unset': 'unset'.

.This error can be due to the fact that ImageMagick is not installed on your computer, or (for Windows users) that you didn't specify the path to the ImageMagick binary in file conf.py, or that the path you specified is incorrect

In [21]:
txt_clip = TextClip("Sc_"+n, fontsize=12, color='white').set_pos("right", "bottom").set_duration(10)
burn_video = CompositeVideoClip([v_clip, txt_clip])

chunk:   0%|          | 33/8872 [00:00<00:37, 236.52it/s, now=None]

Moviepy - Building video /Users/sjegan/Downloads/Review/joker2.mp4.
MoviePy - Writing audio in %s


t:   0%|          | 10/3457 [00:00<00:35, 96.70it/s, now=None]       

MoviePy - Done.
Moviepy - Writing video /Users/sjegan/Downloads/Review/joker2.mp4



Moviepy - Done !
Moviepy - video ready /Users/sjegan/Downloads/Review/joker2.mp4


In [45]:
! pip install foliantcontrib.imagemagick --ignore-installed PyYAML

  Using cached https://files.pythonhosted.org/packages/4d/b0/07003bc87736282ada3f29742ba02bc5e9ac19a394cf75fbae284886bb5f/foliantcontrib.imagemagick-1.0.2-py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/b0/be/952a1682466f81a1464f5f684b2b509d924fcac59ec1778994989103a2d2/foliant-1.0.11-py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/25/5f/cd806f8966594763e9bce169bf5b74fcdfaf1f5a806fa8ef669c4da5e2d6/cliar-1.3.2-py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/87/61/2dfea88583d5454e3a64f9308a686071d58d59a55db638268a6413e1eb6d/prompt_toolkit-2.0.10-py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/73/fb/00a976f728d0d1fecfe898238ce23f502a721c0ac0ecfedb80e0d88c64e9/six-1.12.0-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/7e/9f/526a6947247599b084ee5232e4f9190a38f398d7300d866af3ab571a5bfe/wcwidth-0.1.7-py2.py3-none-any.whl


In [46]:
txt_clip = mpe.TextClip("Sc_", fontsize=12, color='white').set_pos("right", "bottom").set_duration(10)

OSError: MoviePy Error: creation of None failed because of the following error:

[Errno 2] No such file or directory: 'unset': 'unset'.

.This error can be due to the fact that ImageMagick is not installed on your computer, or (for Windows users) that you didn't specify the path to the ImageMagick binary in file conf.py, or that the path you specified is incorrect

    100% |████████████████████████████████| 225kB 2.3MB/s ta 0:00:011
